# TODO:
Use a Holoviews FacetGrid instead Multiple model density, velocity, accumulated sediment DynamicMaps

In [10]:
import xarray as xr
import hvplot.xarray
from JulesD3D.utils import quickDF
# from JulesD3D.processNetCDF import proc
import holoviews as hv
from os import path, walk
import datashader as ds
from IPython.display import Markdown as md
%load_ext autoreload

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [11]:
# depth_bedlayer = trim['DP_BEDLYR'].isel(nlyrp1=slice(0,-1)).transpose('time', 'M', 'N', 'nlyrp1') #, transpose_coords=False
# depth_bedlayer_end = depth_bedlayer.isel(time=-1)
# depth_bedlayer_end.shape
# # dist_between_layers = depth_bedlayer.diff('DP_BDLYR')Grid, makeVelocity, addDepth, addUnderlayerCoords, addVectorSum

### Manually define the models

In [12]:
# open ALL netCDF files in this folder
scenario_results_folder = '/Users/julesblom/ThesisResults/Slope0.85'

models = []

for root, dirs, files in walk(scenario_results_folder):
    for file in sorted(files):
        if file.endswith('nc'):
            models.append({"path": path.join(scenario_results_folder, file),  "title": file[9:14]})

### Or read all netCDF in a folder

In [13]:
models

[{'path': '/Users/julesblom/ThesisResults/Slope0.85/Slope085_Run01.nc',
  'title': 'Run01'},
 {'path': '/Users/julesblom/ThesisResults/Slope0.85/Slope085_Run05.nc',
  'title': 'Run05'},
 {'path': '/Users/julesblom/ThesisResults/Slope0.85/Slope085_Run06.nc',
  'title': 'Run06'},
 {'path': '/Users/julesblom/ThesisResults/Slope0.85/Slope085_Run10.nc',
  'title': 'Run10'},
 {'path': '/Users/julesblom/ThesisResults/Slope0.85/Slope085_Run15.nc',
  'title': 'Run15'},
 {'path': '/Users/julesblom/ThesisResults/Slope0.85/Slope085_Run20.nc',
  'title': 'Run20'},
 {'path': '/Users/julesblom/ThesisResults/Slope0.85/Slope085_Run25.nc',
  'title': 'Run25'},
 {'path': '/Users/julesblom/ThesisResults/Slope0.85/Slope085_Run30.nc',
  'title': 'Run30'},
 {'path': '/Users/julesblom/ThesisResults/Slope0.85/Slope085_Run35.nc',
  'title': 'Run35'},
 {'path': '/Users/julesblom/ThesisResults/Slope0.85/Slope085_Run40.nc',
  'title': 'Run40'},
 {'path': '/Users/julesblom/ThesisResults/Slope0.85/Slope085_Run45.nc'

In [22]:
# array of xarray DataSets
trims = [xr.open_dataset(model_dict['path']) for model_dict in models]

In [28]:
# trims[-1].isel(N=slice(12000,None))

In [15]:
channel_index = int(trims[0].M.size/2)

In [21]:
# sanity check of times, needs to be equal!
times = [trim.time.size for trim in trims]
all_same_time = ((i == trims[0].time.size) for i in times)
all(all_same_time)

True

In [7]:
depth_clim = (-0.5, 0.5)
bottom_diff_datasets_per_run = []

In [8]:
# Ensure that datasets have equal startdates, this is hack for comparing in lineplot with hvplot
same_time = trims[0].time

## Make xarray DataSet with bottom difference per run
Times are all set to first sim time to allow comparison

In [9]:
# bottom difference difference PER RUN
for (i, trim) in enumerate(trims):
    keyword = f"{models[i]['title']}" #_diff
    trim[keyword] = trim.DPS.isel(time=0) - trim.DPS
    
    diff_channel_end = trim[keyword]
    diff_channel_end['time'] = same_time # this is hack for comparing in lineplot with hvplot
    bottom_diff_datasets_per_run.append(diff_channel_end)

In [10]:
ds_diff_per_run = xr.merge(bottom_diff_datasets_per_run, compat='override')
ds_diff_per_run = fixMeshGrid(ds_diff_per_run, mystery_flag=True)

------ Fixing mesh grid, assuming a uniform grid ------
x_gridstep:	 200.0 m
y_gridstep:	 200.0 m
width:		 26000.0 m
length:		 36200.0 m
132 x 182 grid


In [11]:
ds_diff_per_run

<xarray.Dataset>
Dimensions:  (M: 132, N: 182, time: 12)
Coordinates:
    XZ       (M, N) int64 0 0 0 0 0 0 0 ... 26100 26100 26100 26100 26100 26100
    YZ       (M, N) int64 0 200 400 600 800 ... 35400 35600 35800 36000 36200
  * time     (time) datetime64[ns] 2020-02-01 ... 2020-02-01T19:48:00
Dimensions without coordinates: M, N
Data variables:
    Run01    (M, N, time) float32 0.0 0.0 0.0 0.0 0.0 ... 0.0 0.0 0.0 0.0 0.0
    Run05    (M, N, time) float32 0.0 0.0 0.0 0.0 0.0 ... 0.0 0.0 0.0 0.0 0.0
    Run06    (M, N, time) float32 0.0 0.0 0.0 0.0 0.0 ... 0.0 0.0 0.0 0.0 0.0
    Run10    (M, N, time) float32 0.0 0.0 0.0 0.0 0.0 ... 0.0 0.0 0.0 0.0 0.0

In [12]:
ds_diff_per_run.isel(M=channel_index, time=-1).hvplot.line(ylim=depth_clim) # groupby='time',

:NdOverlay   [Variable]
   :Curve   [YZ]   (value)

## Total accumulated sediment over runs

In [13]:
bottom_diff_datasets_cumu = []
# Accumulated bottom difference 
for (i, trim) in enumerate(trims):
    keyword = f"{models[i]['title']}_diff"
    trim[keyword] = trims[0].DPS.isel(time=0) - trim.DPS
    
    diff_channel_end = trim[keyword]
    diff_channel_end['time'] = same_time # this is hack for comparing in lineplot with hvplot
    bottom_diff_datasets_cumu.append(diff_channel_end)

In [14]:
ds_bottom_diff_cumu = xr.merge(bottom_diff_datasets_cumu, compat='override')

In [15]:
ds_bottom_diff_cumu

<xarray.Dataset>
Dimensions:     (M: 132, N: 182, time: 12)
Coordinates:
    XZ          (M, N) float64 ...
    YZ          (M, N) float64 ...
  * time        (time) datetime64[ns] 2020-02-01 ... 2020-02-01T19:48:00
Dimensions without coordinates: M, N
Data variables:
    Run01_diff  (M, N, time) float32 0.0 0.0 0.0 0.0 0.0 ... 0.0 0.0 0.0 0.0 0.0
    Run05_diff  (M, N, time) float32 0.0 0.0 0.0 0.0 0.0 ... 0.0 0.0 0.0 0.0 0.0
    Run06_diff  (M, N, time) float32 0.0 0.0 0.0 0.0 0.0 ... 0.0 0.0 0.0 0.0 0.0
    Run10_diff  (M, N, time) float32 0.0 0.0 0.0 0.0 0.0 ... 0.0 0.0 0.0 0.0 0.0

In [16]:
# fix delft3d shitty output meshgrid with missing values due to enclosure
ds_bottom_diff_total = fixMeshGrid(ds_bottom_diff_cumu,
                                       ds_bottom_diff_cumu.XZ.values, ds_bottom_diff_cumu.YZ.values,
                                       mystery_flag=True)

------ Fixing mesh grid, assuming a uniform grid ------
x_gridstep:	 200.0 m
y_gridstep:	 200.0 m
width:		 26000.0 m
length:		 36200.0 m
132 x 182 grid


In [17]:
ds_bottom_diff_cumu_end = ds_bottom_diff_cumu.isel(time=-1)

In [18]:
map_clim = (-0.3, 0.3)
ds_bottom_diff_cumu.data_vars

Data variables:
    Run01_diff  (M, N, time) float32 0.0 0.0 0.0 0.0 0.0 ... 0.0 0.0 0.0 0.0 0.0
    Run05_diff  (M, N, time) float32 0.0 0.0 0.0 0.0 0.0 ... 0.0 0.0 0.0 0.0 0.0
    Run06_diff  (M, N, time) float32 0.0 0.0 0.0 0.0 0.0 ... 0.0 0.0 0.0 0.0 0.0
    Run10_diff  (M, N, time) float32 0.0 0.0 0.0 0.0 0.0 ... 0.0 0.0 0.0 0.0 0.0

In [19]:
quadmesh_plotting_options = dict(cmap='PiYG', height=550, width=400, clabel='m', clim=map_clim)

all_end_plots = [ds_bottom_diff_cumu_end[model_name].hvplot.quadmesh('XZ', 'YZ', **quadmesh_plotting_options, title=model_name) for model_name in ds_bottom_diff_cumu_end.data_vars]

In [20]:
all_end_plots[0] + all_end_plots[1] + all_end_plots[2]

:Layout
   .QuadMesh.I   :QuadMesh   [XZ,YZ]   (Run01_diff)
   .QuadMesh.II  :QuadMesh   [XZ,YZ]   (Run05_diff)
   .QuadMesh.III :QuadMesh   [XZ,YZ]   (Run06_diff)

In [21]:
all_end_plots[3] #+ all_end_plots[4] + all_end_plots[6]

:QuadMesh   [XZ,YZ]   (Run10_diff)

In [22]:
# all_end_plots[7] 

In [23]:
len(all_end_plots)

4

In [24]:
ds_bottom_diff_cumu

<xarray.Dataset>
Dimensions:     (M: 132, N: 182, time: 12)
Coordinates:
    XZ          (M, N) int64 0 0 0 0 0 0 ... 26100 26100 26100 26100 26100 26100
    YZ          (M, N) int64 0 200 400 600 800 ... 35400 35600 35800 36000 36200
  * time        (time) datetime64[ns] 2020-02-01 ... 2020-02-01T19:48:00
Dimensions without coordinates: M, N
Data variables:
    Run01_diff  (M, N, time) float32 0.0 0.0 0.0 0.0 0.0 ... 0.0 0.0 0.0 0.0 0.0
    Run05_diff  (M, N, time) float32 0.0 0.0 0.0 0.0 0.0 ... 0.0 0.0 0.0 0.0 0.0
    Run06_diff  (M, N, time) float32 0.0 0.0 0.0 0.0 0.0 ... 0.0 0.0 0.0 0.0 0.0
    Run10_diff  (M, N, time) float32 0.0 0.0 0.0 0.0 0.0 ... 0.0 0.0 0.0 0.0 0.0

In [25]:
ds_bottom_diff_cumu_end.isel(M=channel_index).hvplot.line( ylim=(-2,2)) # time=-1

:NdOverlay   [Variable]
   :Curve   [YZ]   (value)

In [26]:
# max_depo_locations = [merged_bottom_diff_cumu_end[model_name].max() for model_name in merged_bottom_diff_cumu_end.data_vars]
# max_depo_locations

In [27]:
ds_bottom_diff_cumu.isel(M=channel_index)

<xarray.Dataset>
Dimensions:     (N: 182, time: 12)
Coordinates:
    XZ          (N) int64 13100 13100 13100 13100 ... 13100 13100 13100 13100
    YZ          (N) int64 0 200 400 600 800 ... 35400 35600 35800 36000 36200
  * time        (time) datetime64[ns] 2020-02-01 ... 2020-02-01T19:48:00
Dimensions without coordinates: N
Data variables:
    Run01_diff  (N, time) float32 0.0 0.0 0.0 0.0 0.0 ... 0.0 0.0 0.0 0.0 0.0
    Run05_diff  (N, time) float32 0.0 0.0 0.0 ... 0.002746582 0.002746582
    Run06_diff  (N, time) float32 0.0 0.0 0.0 ... 0.002746582 0.002746582
    Run10_diff  (N, time) float32 0.0 0.0 0.0 ... 0.0053100586 0.0053100586

# 3D (wow!)

In [29]:
# import pyvista as pv

In [ ]:
# depth_bedlayer = trim['DP_BEDLYR'].isel(nlyrp1=slice(0,-1)).transpose('time', 'M', 'N', 'nlyrp1') #, transpose_coords=False
# depth_bedlayer_end = depth_bedlayer.isel(time=-1)
# depth_bedlayer_end.shape
# # dist_between_layers = depth_bedlayer.diff('DP_BDLYR')

In [ ]:
# x_interfaces = np.repeat(trim.XZ.values[:,:, np.newaxis], nr_of_underlayer_centers, axis=2)
# y_interfaces = np.repeat(trim.YZ.values[:,:, np.newaxis], nr_of_underlayer_centers, axis=2)
# y_interfaces.shape

# x_interface_ravel = np.ravel(x_interfaces)
# y_interface_ravel = np.ravel(y_interfaces)

# depth_bedlayer_end_vals = depth_bedlayer_end.values
# height_deposits_end_vals =  np.flip(depth_bedlayer_end_vals, axis=2)

# depth_bedlayer_end_ravel = np.ravel(depth_bedlayer_end_vals)
# height_deposits_end_ravel = np.ravel(height_deposits_end_vals)

In [ ]:
# xyz_interfaces = np.column_stack((x_interface_ravel, y_interface_ravel, height_deposits_end_ravel))